# Analýza novinových článků

## úvod

Táto práce se zabívá tvorbou jazykového modelu a následnou klasifikací novinových článků.

Jakožto podkladová data byla použita datová sada Czech Text Document Corpus v 2.0 která je veřejně dostupná z url: https://lindat.cz/repository/xmlui/handle/11234/1-2884. V tomto repozitáři nejsou články uloženy v původním stavu, ale již ve zpracovaném a vyčištěném json formátu, který byl přímo použit pro trénování modelu.
    
Jako základní jazykový model byl zvolen word2vec, který ve své době (2013) jako první v oblasti strojového zpracování úspěšně použil neuronové sítě.Dnes je již tento model překonán (dnes je větśina modelů založena na transformátorech jako například BERT, ChatGPT apod.), avšak pro tuto práci tento jednodušší model postačí (transformátory pro úspěšné naučení potřebují větší objemy textu). Jeho implementaci v základní verzi pro framework pytorch lze najít v souboru [model.py](model.py).

Následně byl pro každý dokument vypočten vektor zprůměrováním vektorů pro jednotlivá slova v dokumentu.Pos Nad těmito vektory, byla Pro klasifikaci byla naučená jednoduchá dopředná síť s jednou skrytou vrstvou.

### struktura projektu

* data - Uchovaná zpracovaná data.
    * encoding.json - Slovník mapující unikátní slova k číselnému kódu.
    * category_encoding.json - Slovník mapující zkratkově psanné kategorie k číselnému kódu.
    * dataset.json - Základní sada již číselně zakódovaných dokumentů.
    * train_dataset.json - Výběr dokumentů ze sady pro trénování modelů.
    * test_dataset.json - Výběr dokumentů ze sady pro testování modelů.
    * czech_stopwords.json - Seznam českých výplňových slov.
* model.py - Implementace sití.
* model_system.py - Pomocné třídy, které zajišťují trénování a zpracování dat. Použit [pytorch lightning](https://lightning.ai/pytorch-lightning/).
* data_modules.py - Třídy, které slouží pro přímou obsluhu dat.
* train_embeddings.py - Spouštěcí skript pro trénování jazykového modelu.
* model_embeddings.ckpt - Natrénovaná uložená síť jazykového modelu.
* train_classification.py - Spouštěcí skript pro trénování klasifikační sítě.
* model_classification.ckpt - Natrénovaná síť klasifikačního modelu.

Toto jsou nejdůležitější soubory. Projekt obsahuje více důležitých souborů, ty se ale týkají jen pro správu a strukturování kódu.

### zpracování dat

Všechny soubory byly nejdříve nahrány do dataframu společně s vyparsovanýmá názvama kategorií. Poté byly texty vyčištěny od výplňových slov za pomoci přiloženého slovníku a zbaveny interpunkce. Následně pro zjednodušení byly odstraněny slova (nahrazeno znakem _) s výskytem >= 20.

### word2vec

Tento model má 2 varianty s názvy Skipgram a CBOW. V této práci byl konkrétně použit skipgram. Obě verze byli prědstaveny zároveń v puvodní práci a nejsou nijak významně odlišná. Obě varianty vycházejí ze stejné idei, jen mají zcela opačné úlohy. Skipgram se snaží na základě slova předpovídat kontextová slova, CBOW opačně předpovídá slovo na základě kontextu. Tyto úlohy jsou pouze doprovodné a dále se pak pouźívá jen první vrstva.

po naučení tedy můžeme na tuto síť přirovnat k tabulce která mapuje slova na vektory,pro které platí že vektory které reprezentují podobné významy (např král, královna) se nacházejí blízko sebe. 

#### implementační rozdíly

Autor v původní práci popsal první vrstvu jako dopřednou síť bez aktivace. Dovolil jsem si použít modernější vrstvu [Embedding](https://pytorch.org/docs/stable/generated/torch.nn.Embedding.html), která je početně úspornější (nepoužívá maticové násobení ale hledá a navrací sloupec vah).

Dále autor použil v konečné vrstvě hiearchický softmax jako aktivační funkci, z důvodů jednoduchosti jsem použil obyčejný softmax.

## importy a nastavení

In [1]:
from math import sqrt
from pathlib import Path

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import plotly_express as px
import seaborn as sns
import torch
from umap import UMAP

from _dataclasses import EncodedTextDataset
from data_modules import DocumentDataModule 
from model_system import DocumentClassifier, word2vec
from utils import   sort_confusion_matrices

plt.rcParams["figure.figsize"] = (100,100)
plt.rcParams["font.size"] = (62) 

/home/dave/prace/ing_studium/CRS/seminarka/.venv/lib/python3.11/site-packages/umap/distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/home/dave/prace/ing_studium/CRS/seminarka/.venv/lib/python3.11/site-packages/umap/distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/home/dave/prace/ing_studium/CRS/seminarka

In [2]:
def make_heatmaps(matrices: torch.Tensor, matrix_indices: torch.Tensor, format: str= ""):
    fig_size = int(sqrt(len(matrix_indices)))
    fig,axes = plt.subplots(fig_size,fig_size)
    for index, matrix_index in enumerate(matrix_indices):
        sns.heatmap(
        matrices[matrix_index].numpy(),
        annot=True,
        fmt=format,
        ax= axes[index//fig_size][index%fig_size], 
        cbar=False
        )
        axes[index//fig_size][index%fig_size].set_title(train_dataset.category_encoding["word"].to_numpy()[matrix_index])

## word2vec model

### načtení modelu

In [3]:
dataset= EncodedTextDataset.load()
embedder = word2vec.load_from_checkpoint("model_embedding.ckpt")

### zobrazení latentního prostoru slov

Z modelu jsou vyextrahovány vektory pro všechna slova ve slovníku a následně aplikací UMAP algoritmu zredukovány z 100 dimenzionálního prostoru do 2 dimenzionálního prostoru.

In [4]:
embedding = embedder.embedding_words(dataset)
proj =\
    UMAP(n_components=2, n_neighbors = 4, min_dist = 0.2, random_state=0)\
    .fit_transform(embedding.drop("word",axis=1))
df = pd.DataFrame(proj, columns = ["x", "y"])
df["word"] = embedding["word"]
px.scatter(df, x='x', y='y', width = 1500, height = 1000, hover_name = "word", hover_data = {"x":False, "y":False})

### zobrazení latentního prostoru článků

U článků jsou vektory zobrazeny stejně,jen vektory jsou vyextrahovány zprůměrováním slovních vektorů v jednotlivých člansích a UMAP má jiné parametry.

In [5]:
documents = embedder.embedding_encoded_documents(dataset)

proj =\
    UMAP(n_components=2, n_neighbors = 12, min_dist = 0.2, random_state=0)\
    .fit_transform(documents.drop("category",axis=1))
proj = pd.DataFrame(proj)
proj["category"] = documents["category"]
proj =  dataset.decode_categories(proj.explode("category", ignore_index=True))

fig = px.scatter(
    proj,
    x=0,
    y=1,
    width = 1500,
    height = 1000,
    hover_name = "category",
    color="category",
)
fig = fig.update_traces(marker={"size": 5})

buttons = [
    {
        "label": "all",
        "method": "restyle",
        "args": [
            {"opacity": 1}
        ]
    }
]
buttons.extend(            
    [
        {
            "label": trace.name,
            "method": "restyle",
            "args": [
                {"opacity": [1 if vis_index == trace_index else 0.01 for vis_index, _ in enumerate(fig.data)]}
            ]
        }
        for trace_index,trace in enumerate(fig.data)
    ]
)
fig.update_layout(
    hovermode= False,
    updatemenus=[
        {
        "buttons": buttons
        }
    ]
)

## kategorizace článků

### načtení modelu

In [6]:
classifier = DocumentClassifier.load_from_checkpoint("model_classifier.ckpt")

train_dataset = EncodedTextDataset.load(Path("./data/train_dataset.json"))
test_dataset = EncodedTextDataset.load(Path("./data/test_dataset.json"))
datamodule = DocumentDataModule(
    train_dataset,
    test_dataset,
    test_dataset
)

/home/dave/prace/ing_studium/CRS/seminarka/.venv/lib/python3.11/site-packages/lightning/pytorch/utilities/parsing.py:197: UserWarning:

Attribute 'embedder' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['embedder'])`.



### hledání prahu rozdělení

Pro vyhledání je vyzkoušeno 20 hodnot v rozmezí <0,1>. Pro každé rozdělení je vypočteno f1 skóre (harmonický průměr pro specifitu a přesnost) s makro průměrem. Z nejlepšího rozdělení je vzata matice záměn.

In [7]:
matrices,matricies_normalized, split, score = classifier.find_best_decision_split(
    datamodule=datamodule,
    beta=1.
)

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


split: 0.0


/home/dave/prace/ing_studium/CRS/seminarka/.venv/lib/python3.11/site-packages/torchmetrics/utilities/prints.py:36: UserWarning:

120 NaN values found in confusion matrix have been replaced with zeros.



score:0.08364038914442062

split: 0.05263157933950424


/home/dave/prace/ing_studium/CRS/seminarka/.venv/lib/python3.11/site-packages/torchmetrics/utilities/prints.py:36: UserWarning:

4 NaN values found in confusion matrix have been replaced with zeros.



score:0.08992671966552734

split: 0.10526315867900848
score:0.09952114522457123

split: 0.15789473056793213
score:0.11312501132488251

split: 0.21052631735801697
score:0.1289394497871399

split: 0.2631579041481018
score:0.14924411475658417

split: 0.31578946113586426
score:0.17220363020896912

split: 0.3684210479259491
score:0.19751794636249542

split: 0.42105263471603394
score:0.22624078392982483

split: 0.4736842215061188
score:0.2579605281352997

split: 0.5263158082962036
score:0.28831005096435547

split: 0.5789473652839661
score:0.32103967666625977

split: 0.6315789222717285
score:0.3485599160194397

split: 0.6842105388641357
score:0.36919787526130676

split: 0.7368420958518982
score:0.39045679569244385

split: 0.7894736528396606
score:0.3856290578842163

split: 0.8421052694320679
score:0.36586472392082214

split: 0.8947368264198303
score:0.315539687871933

split: 0.9473684430122375
score:0.22435036301612854

split: 1.0
score:0.0



In [8]:
print(f"nejlepší nalezené rozdělení:     hranice: {split}  f1 skóre: {score}")

nejlepší nalezené rozdělení:     hranice: 0.7368420958518982  f1 skóre: 0.39045679569244385


### výsledné matice záměn

setřídění matic podle četností kategorie (součet spodního řádku matice) a vizualizace matic pro prvních 9 kategorií.

In [9]:
sorted_matrices, sorted_indices = sort_confusion_matrices(matrices)

In [10]:
make_heatmaps(matrices, sorted_indices[:9], format=",d")

### výsledná matice záměn (normováno)

In [11]:
make_heatmaps(matricies_normalized, sorted_indices[:9],format=".3f")

 ## zdroje

MIKOLOV, Tomáš, Kai CHEN, Greg CORRADO a Jeffrey DEAN. Efficient Estimation of Word Representations in Vector Space [online]. 2013, 12 [cit. 2023-06-04]. Dostupné z: doi:https://doi.org/10.48550/arXiv.1301.3781

MIKOLOV, Tomáš. Distributed Representations of Sentences and Documents [online]. 9 [cit. 2023-06-04]. Dostupné z: doi:https://doi.org/10.48550/arXiv.1405.4053

### data

https://lindat.cz/repository/xmlui/handle/11234/1-2884